# Проект по созданию умного поисковика в документах

### Скачивания необходимых библиотек

In [4]:
# Библиотека для чтения word файлов(.docx) 
!pip install Spire.Doc

  Using cached spire_doc-13.12.0-py3-none-win_amd64.whl.metadata (14 kB)
  Using cached plum_dispatch-1.7.4-py3-none-any.whl.metadata (1.8 kB)
Using cached spire_doc-13.12.0-py3-none-win_amd64.whl (28.2 MB)
Using cached plum_dispatch-1.7.4-py3-none-any.whl (24 kB)


In [273]:
# Библиотека для обработки обработка естественного языка(NLP)
!pip install nltk

  Using cached click-8.3.1-py3-none-any.whl.metadata (2.6 kB)
   ---------------------------------------- 0.0/1.5 MB ? eta -:--:--
   -------------------- ------------------- 0.8/1.5 MB 8.5 MB/s eta 0:00:01
   ---------------------------------------- 1.5/1.5 MB 8.9 MB/s  0:00:00
Using cached click-8.3.1-py3-none-any.whl (108 kB)

   ---------------------------------------- 0/4 [tqdm]
   ---------------------------------------- 0/4 [tqdm]
   ---------- ----------------------------- 1/4 [regex]
   -------------------- ------------------- 2/4 [click]
   -------------------- ------------------- 2/4 [click]
   ------------------------------ --------- 3/4 [nltk]
   ------------------------------ --------- 3/4 [nltk]
   ------------------------------ --------- 3/4 [nltk]
   ------------------------------ --------- 3/4 [nltk]
   ------------------------------ --------- 3/4 [nltk]
   ------------------------------ --------- 3/4 [nltk]
   ------------------------------ --------- 3/4 [nltk]
   --

In [279]:
# Установка русских стоп слов
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Matwei\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [185]:
# Установка новой версии токенайзера
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\Matwei\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

In [284]:
# Библиотека для морфологического анализа
!pip install pymorphy3

   ---------------------------------------- 0.0/8.4 MB ? eta -:--:--
   ---- ----------------------------------- 1.0/8.4 MB 8.4 MB/s eta 0:00:01
   ------------- -------------------------- 2.9/8.4 MB 8.8 MB/s eta 0:00:01
   ----------------------- ---------------- 5.0/8.4 MB 9.2 MB/s eta 0:00:01
   ------------------------------- -------- 6.6/8.4 MB 8.8 MB/s eta 0:00:01
   -------------------------------------- - 8.1/8.4 MB 8.5 MB/s eta 0:00:01
   ---------------------------------------- 8.4/8.4 MB 8.4 MB/s  0:00:01

   ------------- -------------------------- 1/3 [dawg2-python]
   -------------------------- ------------- 2/3 [pymorphy3]
   -------------------------- ------------- 2/3 [pymorphy3]
   ---------------------------------------- 3/3 [pymorphy3]

Note: you may need to restart the kernel to use updated packages.


### Подключение библиотек

In [8]:
import pandas as pd, numpy as np, os, string, re, nltk, pymorphy3

from pickle import dump
from datetime import datetime
from spire.doc import Document
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity as sklearn_cosine

## Создания датасета из файлов

##### Переменные с путями до папок с файлами(.docx, .md)

In [167]:
path_to_word_file = 'docs_for_model/word_files'
path_to_markdown_file = 'docs_for_model/md_files'

##### Функция для чтения word файлов(.docx), получения текста из него, названия файла и даты последнего изменения

In [168]:
def get_text_in_word_file(path_to_file: str) -> str:
    if (extension:=os.path.splitext(os.path.basename(path_to_file))[1]) != '.doc' and extension != '.docx':
        return None
    doc = Document()
    doc.LoadFromFile(path_to_file)
    text = doc.GetText()
    del doc
    name_file = os.path.basename(path_to_file)
    date_last_modified_file = datetime.fromtimestamp(os.path.getmtime(path_to_file)).strftime("%d-%m-%Y %H:%M")
    return text[71:], name_file, date_last_modified_file

##### Функция для чтения markdown файлов(.md), получения текста из него, названия файла и даты последнего изменения

In [169]:
def get_text_in_markdown_file(path_to_file: str) -> str:
    if os.path.splitext(os.path.basename(path_to_file))[1] != '.md':
        return None
    with open(path_to_file, 'r', encoding='utf-8') as file:
        text = file.read()
    name_file = os.path.basename(path_to_file)
    date_last_modified_file = datetime.fromtimestamp(os.path.getmtime(path_to_file)).strftime("%d-%m-%Y %H:%M")
    return text, name_file, date_last_modified_file

##### Проверка работоспособности функций

In [172]:
get_text_in_word_file('./docs_for_model/word_files/Создание SchedulerUser.docx')

('\r\nСоздание пользователя «SchedulerUser» \r\nПользователь «SchedulerUser» используется планировщиком задач.\r\nПримечание: Функции планировщика задач указаны в «Руководства администратора Lexema-ECM» https://ecm-administrator-manuals.readthedocs.io/ru/latest/Admin%20manuals/Функции%20планировщика%20задач/)\r\nДля создания пользователя перейти в документ «Управление пользователями», нажать кнопку «Создание пользователя», заполнить поля. В качестве логина рекомендуется указать SchedulerUser. Нажать на сохранить.\r\n\r\nЕсли организаций на проекте несколько, необходимо привязать созданного пользователяко всем остальным организациям. Выбрать пользователя SchedulerUser, нажать кнопку «Данные пользователя», в окне «Организации» выбрать необходимые организации галочками слева в строках, где не стоит галочка Зарегистрир., заполнить галочку «Переносить роли в новую организацию», нажать «Сохранить».\r\n\r\nЧерез кнопку «Управление компаниями» из меню, открывающемуся по клику на логин текущего

In [173]:
get_text_in_markdown_file('./docs_for_model/md_files/description.md')

('# Lexema-ECM. Введение\n\n## Введение\n\n**Lexema-ECM** — комплексная система управления корпоративным контентом, включающая в себя автоматизацию работы с кадровыми документами.\n\nРуководство предназначено:\n\n- для специалистов, которым необходимо обрабатывать электронные документы в Lexema-ECM: создавать карточки, отправлять по маршруту согласования и подписывать документы электронной подписью;\n\n## Назначение Lexema-ECM\n\n**Lexema-ECM**  имеет богатый функционал типовой конфигурации — от канцелярии до юридически значимого кадрового документооборота, а также широкие возможности для развития системы и подключения дополнительных функций. \nВ системе настроены типовые карточки по работе с договорами, письмами, поручениями, служебными записками, приказами, заявления от сотрудников и ЛНА по кадровому документообороту, а также преднастроены маршруты по их обработке. Документы готовы к использованию сразу после развертывания системы. Поэтому можно в кратчайший срок начать получать бону

##### Добавления данных в датасет

In [174]:
# функция для получения словаря из данных
def create_dict_data(path_to_dir: str, function) -> dict:
    dict_data = {
        'name_file' : [],
        'text_file' : [],
        'date_last_modified_file' : [],
    }
    for path in os.listdir(path_to_dir):
        data_file = function(f'{path_to_dir}/{path}')
        if not data_file:
            continue
        dict_data['name_file'].append(data_file[1])
        dict_data['text_file'].append(data_file[0])
        dict_data['date_last_modified_file'].append(data_file[2])
    return dict_data

In [175]:
# Список с датасетами
lst_df = [
    pd.DataFrame(create_dict_data(path_to_word_file, get_text_in_word_file)), 
    pd.DataFrame(create_dict_data(path_to_markdown_file, get_text_in_markdown_file))
]

In [176]:
# Готовый датасет
df = pd.concat(lst_df)

In [178]:
df.shape

(417, 3)

In [180]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 417 entries, 0 to 414
Data columns (total 3 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   name_file                417 non-null    object
 1   text_file                417 non-null    object
 2   date_last_modified_file  417 non-null    object
dtypes: object(3)
memory usage: 13.0+ KB


In [177]:
df.head(10)

name_file  \
0                        Создание SchedulerUser.docx   
1  ТЗ_ОВВК_ОМТС_Склад_Комплектация_Закупки_от_19_...   
0                                     description.md   
1                                       index (1).md   
2                                      index (10).md   
3                                     index (100).md   
4                                     index (101).md   
5                                     index (102).md   
6                                     index (103).md   
7                                     index (104).md   

                                           text_file date_last_modified_file  
0  \r\nСоздание пользователя «SchedulerUser» \r\n...        02-12-2025 15:02  
1  n.\r\nОглавление\r\nКомплектация ОВКК\t2\r\n1....        27-11-2025 16:00  
0  # Lexema-ECM. Введение\n\n## Введение\n\n**Lex...        08-12-2025 12:09  
1  # FAQ Lexema-ECM\n\n## Работа с документами и ...        02-12-2025 15:02  
2  ---\nsearch:\n  boost: 2 \n---\n# Выпуск облач...        02-12-2025 15:02  
3  # Справочник полномочий\n\n## Описание\n\n**По...        08-12-2025 12:09  
4  # Сотрудники\n\n## Общее описание назначения с...        08-12-2025 12:09  
5  # Создание документа в мобильном приложении\n\...        08-12-2025 12:09  
6  # Работа с документами в мобильном приложении\...        08-12-2025 12:09  
7  # Совещание\n\n## Описание\n\nВ данной статье ...        08-12-2025 12:09

##### Сохранения датасета

In [181]:
df.to_csv('data_from_documentation.csv')

## Предобработка данных

In [2]:
df = pd.read_csv('data_from_documentation.csv').drop('Unnamed: 0', axis=1)

In [3]:
df

name_file  \
0                          Создание SchedulerUser.docx   
1    ТЗ_ОВВК_ОМТС_Склад_Комплектация_Закупки_от_19_...   
2                                       description.md   
3                                         index (1).md   
4                                        index (10).md   
..                                                 ...   
412                           Управление компаниями.md   
413                        Управление производством.md   
414                            Управление ремонтами.md   
415                                  Учет договоров.md   
416     Учет товарно-материальных ценностей и услуг.md   

                                             text_file date_last_modified_file  
0    \r\nСоздание пользователя «SchedulerUser» \r\n...        02-12-2025 15:02  
1    n.\r\nОглавление\r\nКомплектация ОВКК\t2\r\n1....        27-11-2025 16:00  
2    # Lexema-ECM. Введение\n\n## Введение\n\n**Lex...        08-12-2025 12:09  
3    # FAQ Lexema-ECM\n\n## Работа с документами и ...        02-12-2025 15:02  
4    ---\nsearch:\n  boost: 2 \n---\n# Выпуск облач...        02-12-2025 15:02  
..                                                 ...                     ...  
412  # Управление компаниями (Настройка своей орган...        27-11-2025 16:00  
413  # Управение производством\n\n- [Составы издели...        27-11-2025 16:00  
414  ## Дефектная ведомость \n**Дефектная ведомость...        27-11-2025 16:00  
415  # Учет договоров \n\n- [Договоры](./Договоры/Д...        27-11-2025 16:00  
416  # Учет товарно-материальных ценностей и услуг\...        27-11-2025 16:00  

[417 rows x 3 columns]

In [12]:
# Русские стоп слова
russian_stopwords = stopwords.words("russian")
russian_stopwords.extend(['т.д.', 'т', 'д', 'это','который','с','своём','всем','наш', 'свой']) 

# Лемматизация
morph = pymorphy3.MorphAnalyzer(lang='ru')

# Функция для удаления ссылок
def remove_link(text: str) -> str: 
    return re.sub(r'http://.+|https://.+', '', text, flags=re.I)

# Функция для удаления ссылок markdown 
def remove_link_markdown(text: str) -> str: 
    return re.sub(r'\[\w+\]\(.+\)', ' ', text, flags=re.I)

# Функция для удаления html-тегов
def remove_html_tags(text: str) -> str: 
    return re.sub(r'(</[a-z]+>|<[a-z]+>)', ' ', text, flags=re.I)

# Функция для удаления знаков препинания
def remove_punctuation(text: str) -> str: 
    return "".join([ch if ch not in string.punctuation else ' ' for ch in text])

# Функция для удаления чисел
def remove_numbers(text: str) -> str:
    return ''.join([i if not i.isdigit() else ' ' for i in text])

# Функция для удаления лишних пробелов
def remove_multiple_spaces(text: str) -> str:
    return re.sub(r'\s+', ' ', text, flags=re.I)

# Функция для специальных символов
st = '❯\xa0—«»–'
def remove_othersymbol(text: str) -> str:
    return ''.join([ch if ch not in st else ' ' for ch in text])
    
# Функция для удаления одиночных символов
def remove_single_symbol(text: str) -> str:
    return re.sub(r' [a-zа-яё] ', ' ', text, flags=re.I)
    
# Функция для удаления стоп слов и лемматизации текста
def lemmatization_of_text(text: str) -> str:
    try:
        tokens = word_tokenize(text)
        tokens = [token for token in tokens if token not in russian_stopwords]
        res = list()
        for word in tokens:
            p = morph.parse(word)[0]
            res.append(p.normal_form)
        text = " ".join(res)
        return text
    except Exception as e:
        return f'Ошибка: {e}'

##### Функция для предобработки текста

In [5]:
def text_preprocessing(text: str) -> str:
    text = text.lower()
    text = remove_link_markdown(text)
    text = remove_link(text)
    text = remove_html_tags(text)
    text = remove_punctuation(text)
    text = remove_numbers(text)
    text = remove_othersymbol(text)
    text = remove_single_symbol(text)
    text = remove_multiple_spaces(text)
    text = text.strip()
    text = lemmatization_of_text(text)
    return text

In [6]:
df['text_preprocessing'] = df['text_file'].apply(lambda text: text_preprocessing(text))

In [7]:
df['text_file'][0]

'\r\nСоздание пользователя «SchedulerUser» \r\nПользователь «SchedulerUser» используется планировщиком задач.\r\nПримечание: Функции планировщика задач указаны в «Руководства администратора Lexema-ECM» https://ecm-administrator-manuals.readthedocs.io/ru/latest/Admin%20manuals/Функции%20планировщика%20задач/)\r\nДля создания пользователя перейти в документ «Управление пользователями», нажать кнопку «Создание пользователя», заполнить поля. В качестве логина рекомендуется указать SchedulerUser. Нажать на сохранить.\r\n\r\nЕсли организаций на проекте несколько, необходимо привязать созданного пользователяко всем остальным организациям. Выбрать пользователя SchedulerUser, нажать кнопку «Данные пользователя», в окне «Организации» выбрать необходимые организации галочками слева в строках, где не стоит галочка Зарегистрир., заполнить галочку «Переносить роли в новую организацию», нажать «Сохранить».\r\n\r\nЧерез кнопку «Управление компаниями» из меню, открывающемуся по клику на логин текущего 

In [8]:
df['text_preprocessing'][0]

'создание пользователь scheduleruser пользователь scheduleruser использоваться планировщик задача примечание функция планировщик задача указать руководство администратор lexema ecm создание пользователь перейти документ управление пользователь нажать кнопка создание пользователь заполнить поле качество логин рекомендоваться указать scheduleruser нажать сохранить организация проект несколько необходимо привязать создать пользователяко остальной организация выбрать пользователь scheduleruser нажать кнопка дать пользователь окно организация выбрать необходимый организация галочка слева строка стоить галочка зарегистрир заполнить галочка переносить роль новый организация нажать сохранить кнопка управление компания меню открываться клик логин текущий пользователь требоваться статус администратор перейти организация форма компания окно управление сотрудник найти логин scheduleruser нажать строка форма сотрудник поле статус выбрать администратор также назначить роль ecm admin выбрать её созда

In [9]:
df['text_file'][10]

'# Служебные записки\n\nДокумент «Служебная записка» служит для автоматизации документооборота служебных записок в организации. \n\n![Меню](media/menu.png)\n\nТиповой бизнес-процесс в данном модуле состоит из четырех этапов.\n\n| Этап | Описание |\n| ---- | -------- |\n1 этап | Инициатор создает документ "Служебная записка" из реестра служебных записок. В нем заполняет все необходимые поля и отправляет по маршруту.\n2 этап | Руководитель принимает документ и подписывает его на своем этапе\n3 этап | Документ отправляется на дополнительное согласование\n4 этап | Документ рассматривается адресатами\n\n## Создание новой служебной записки\n\nДля создания служебной записки необходимо открыть "Меню" и в поиске меню ввести - "Служебные записки".\n\n![Реестр](media/reestr.png)\n\nОткроется форма документа "Служебная записка"\n\n![рисунок](media/forma.png)\n\n# Регистрация\n\n**Тип документа** - выбирается из справочника в форме выпадающего списка со строкой быстрого поиска.\n\n**Срочность** - и

In [10]:
df['text_preprocessing'][10]

'служебный записка документ служебный записка служить автоматизация документооборот служебный записка организация типовой бизнес процесс данный модуль состоять четыре этап этап описание этап инициатор создавать документ служебный записка реестр служебный записка немой заполнять необходимый поле отправлять маршрут этап руководитель принимать документ подписывать свой этап этап документ отправляться дополнительный согласование этап документ рассматриваться адресат создание новый служебный записка создание служебный записка необходимо открыть меню поиск меню ввести служебный записка открыться форма документ служебный записка регистрация тип документ выбираться справочник форма выпадать список строка быстрый поиск срочность выпадать список присваиваться срочность документ рег дать номер присваиваться подписание документ действие подписать маршрут номер также присвоиться делегирование задача подписант другой сотрудник присвоить номер вручную автоматически заполняться текущий дата приоритет 

In [11]:
text = ' '.join([i for i in df['text_preprocessing']])
text

'создание пользователь scheduleruser пользователь scheduleruser использоваться планировщик задача примечание функция планировщик задача указать руководство администратор lexema ecm создание пользователь перейти документ управление пользователь нажать кнопка создание пользователь заполнить поле качество логин рекомендоваться указать scheduleruser нажать сохранить организация проект несколько необходимо привязать создать пользователяко остальной организация выбрать пользователь scheduleruser нажать кнопка дать пользователь окно организация выбрать необходимый организация галочка слева строка стоить галочка зарегистрир заполнить галочка переносить роль новый организация нажать сохранить кнопка управление компания меню открываться клик логин текущий пользователь требоваться статус администратор перейти организация форма компания окно управление сотрудник найти логин scheduleruser нажать строка форма сотрудник поле статус выбрать администратор также назначить роль ecm admin выбрать её созда

In [12]:
from nltk.probability import FreqDist
most_words = FreqDist(word_tokenize(text))
print(most_words.most_common(30))

[('документ', 9466), ('png', 3395), ('пользователь', 2652), ('поле', 2457), ('необходимо', 2131), ('кнопка', 2101), ('который', 1995), ('media', 1946), ('and', 1935), ('форма', 1850), ('сотрудник', 1841), ('coalesce', 1750), ('система', 1678), ('настройка', 1642), ('image', 1576), ('реестр', 1489), ('as', 1481), ('маршрут', 1475), ('выбрать', 1457), ('нажать', 1419), ('справочник', 1341), ('создание', 1281), ('дата', 1256), ('договор', 1220), ('создать', 1156), ('вкладка', 1141), ('тип', 1133), ('дать', 1131), ('отпуск', 1104), ('наименование', 1101)]


## Векторизация данных

## Поиск документа по введённой строке

##### Будет сделано несколько видов поиска документа:
- ##### по названию документа;
- ##### по содержанию документа.

##### Поиск по содержимому документа будет дополнятся позиций, где было найденно сходство

#### Для преобразования данных в векторы, будет использован метод TF-IDF

#### Для поиска по содержанию будет использован метод косинового сходства

In [865]:
# Отключение научной степени при выводе
np.set_printoptions(suppress=True)

##### Инициализация тестовых данных


In [1016]:
test_document = 'description.md'
test_text = '**Lexema-ECM**  имеет богатый функционал типовой конфигурации — от канцелярии до юридически значимого кадрового документооборота, а также широкие возможности для развития системы и подключения дополнительных функций. В системе настроены типовые карточки по работе с договорами, письмами, поручениями, служебными записками, приказами, заявления от сотрудников и ЛНА по кадровому документообороту, а также преднастроены маршруты по их обработке. Документы готовы к использованию сразу после развертывания системы. Поэтому можно в кратчайший срок начать получать бонусы от электронного согласования документов.          '
prep_test_text = text_preprocessing(test_text)
test_df = pd.DataFrame({'text_preprocessing' : [prep_test_text]})

##### Инициализация векторизатора

In [14]:
vectorizer = TfidfVectorizer(max_df=0.8, max_features=5000,
                                 min_df=0.01, stop_words=russian_stopwords,
                                 ngram_range=(1,5))

##### Создания датасета для векторизации

In [868]:
concat_df_test = pd.concat([df, test_df], ignore_index=True)['text_preprocessing']

In [869]:
concat_df_test

0      создание пользователь scheduleruser пользовате...
1      n оглавление комплектация овкк дефектный ведом...
2      lexema ecm введение введение lexema ecm компле...
3      faq lexema ecm работа документ маршрут questio...
4      search boost выпуск облачный неквалифицированн...
                             ...                        
413    управение производство состав изделие состав и...
414    дефектный ведомость дефектный ведомость относи...
415    учёт договор вид договор вид договор вид догов...
416    учёт товарный материальный ценность услуга кон...
417    lexema ecm иметь богатый функционал типовой ко...
Name: text_preprocessing, Length: 418, dtype: object

##### Создание TF-IDF матрицы

In [870]:
tfidf_matrix = vectorizer.fit_transform(concat_df_test)

##### Создание матрицы косинового сходства

In [871]:
similarity_matrix = sklearn_cosine(tfidf_matrix)

In [872]:
print(similarity_matrix)

[[1.         0.01902119 0.14351388 ... 0.00335651 0.11583567 0.0506376 ]
 [0.01902119 1.         0.03452442 ... 0.0443777  0.32780475 0.0407073 ]
 [0.14351388 0.03452442 1.         ... 0.02853022 0.04140196 0.50513884]
 ...
 [0.00335651 0.0443777  0.02853022 ... 1.         0.03606934 0.06761607]
 [0.11583567 0.32780475 0.04140196 ... 0.03606934 1.         0.02436596]
 [0.0506376  0.0407073  0.50513884 ... 0.06761607 0.02436596 1.        ]]


In [873]:
similarity_matrix[::-1][0]

array([0.0506376 , 0.0407073 , 0.50513884, 0.07941597, 0.05446156,
       0.01044919, 0.07913859, 0.0613981 , 0.07228565, 0.00780026,
       0.18910172, 0.10075955, 0.11706146, 0.01571374, 0.0108045 ,
       0.0088778 , 0.0794135 , 0.10882199, 0.12156467, 0.02657315,
       0.09056485, 0.03130975, 0.03620973, 0.03445534, 0.13358175,
       0.05399139, 0.        , 0.0488003 , 0.00777595, 0.00894235,
       0.01564856, 0.08386359, 0.06763929, 0.11483265, 0.00804149,
       0.02924167, 0.01702019, 0.00500295, 0.06360181, 0.02439828,
       0.01994611, 0.03074963, 0.09366468, 0.00351705, 0.03535595,
       0.04832551, 0.05837729, 0.00741813, 0.        , 0.14331578,
       0.03142674, 0.08801073, 0.06827908, 0.04205765, 0.09740355,
       0.00157236, 0.05231724, 0.07542347, 0.01720823, 0.        ,
       0.0421338 , 0.0333586 , 0.00643589, 0.06708893, 0.01156498,
       0.05057862, 0.00407604, 0.11964748, 0.02395999, 0.01740499,
       0.02126528, 0.01039721, 0.08923487, 0.0105612 , 0.11039

In [874]:
similarity_matrix[::-1][0][:len(similarity_matrix)-1]

array([0.0506376 , 0.0407073 , 0.50513884, 0.07941597, 0.05446156,
       0.01044919, 0.07913859, 0.0613981 , 0.07228565, 0.00780026,
       0.18910172, 0.10075955, 0.11706146, 0.01571374, 0.0108045 ,
       0.0088778 , 0.0794135 , 0.10882199, 0.12156467, 0.02657315,
       0.09056485, 0.03130975, 0.03620973, 0.03445534, 0.13358175,
       0.05399139, 0.        , 0.0488003 , 0.00777595, 0.00894235,
       0.01564856, 0.08386359, 0.06763929, 0.11483265, 0.00804149,
       0.02924167, 0.01702019, 0.00500295, 0.06360181, 0.02439828,
       0.01994611, 0.03074963, 0.09366468, 0.00351705, 0.03535595,
       0.04832551, 0.05837729, 0.00741813, 0.        , 0.14331578,
       0.03142674, 0.08801073, 0.06827908, 0.04205765, 0.09740355,
       0.00157236, 0.05231724, 0.07542347, 0.01720823, 0.        ,
       0.0421338 , 0.0333586 , 0.00643589, 0.06708893, 0.01156498,
       0.05057862, 0.00407604, 0.11964748, 0.02395999, 0.01740499,
       0.02126528, 0.01039721, 0.08923487, 0.0105612 , 0.11039

##### Получение максимального индекса в косиновом сходстве

In [875]:
int(similarity_matrix[::-1][0][:len(similarity_matrix)-1].argmax())

2

In [876]:
np.argpartition(similarity_matrix[::-1][0][:len(similarity_matrix)-1], -1)[-5:][::-1]

array([  2,  95, 280, 278,  10])

In [877]:
float(similarity_matrix[::-1][0][2])

0.505138839812973

##### Проверка на правильность работы

In [878]:
test_document

'description.md'

In [879]:
df.loc[2]

name_file                                                     description.md
text_file                  # Lexema-ECM. Введение\n\n## Введение\n\n**Lex...
date_last_modified_file                                     08-12-2025 12:09
text_preprocessing         lexema ecm введение введение lexema ecm компле...
Name: 2, dtype: object

### Поиск сходста внутри документа

In [1017]:
text_document = df.loc[2].text_preprocessing

In [1018]:
text_document

'lexema ecm введение введение lexema ecm комплексный система управление корпоративный контент включать автоматизация работа кадровый документ руководство предназначить специалист который необходимо обрабатывать электронный документ lexema ecm создавать карточка отправлять маршрут согласование подписывать документ электронный подпись назначение lexema ecm lexema ecm иметь богатый функционал типовой конфигурация канцелярия юридически значимый кадровый документооборот также широкий возможность развитие система подключение дополнительный функция система настроить типовой карточка работа договор письмо поручение служебный записка приказ заявление сотрудник лна кадровый документооборот также преднастроить маршрут обработка документ готовый использование сразу развёртывание система поэтому краткий срок начать получать бонус электронный согласование документ lexema ecm встроить сервис позволять один нажатие кнопка выпускать облачный неквалифицированный электронный подпись сотрудник компания ис

In [1019]:
prep_test_text

'lexema ecm иметь богатый функционал типовой конфигурация канцелярия юридически значимый кадровый документооборот также широкий возможность развитие система подключение дополнительный функция система настроить типовой карточка работа договор письмо поручение служебный записка приказ заявление сотрудник лна кадровый документооборот также преднастроить маршрут обработка документ готовый использование сразу развёртывание система поэтому краткий срок начать получать бонус электронный согласование документ'

In [1020]:
tokenize_text_document = word_tokenize(text_document)

In [1021]:
tokenize_text_test = word_tokenize(prep_test_text)

In [1022]:
concat_text = tokenize_text_document + tokenize_text_test

In [1023]:
concat_text

['lexema',
 'ecm',
 'введение',
 'введение',
 'lexema',
 'ecm',
 'комплексный',
 'система',
 'управление',
 'корпоративный',
 'контент',
 'включать',
 'автоматизация',
 'работа',
 'кадровый',
 'документ',
 'руководство',
 'предназначить',
 'специалист',
 'который',
 'необходимо',
 'обрабатывать',
 'электронный',
 'документ',
 'lexema',
 'ecm',
 'создавать',
 'карточка',
 'отправлять',
 'маршрут',
 'согласование',
 'подписывать',
 'документ',
 'электронный',
 'подпись',
 'назначение',
 'lexema',
 'ecm',
 'lexema',
 'ecm',
 'иметь',
 'богатый',
 'функционал',
 'типовой',
 'конфигурация',
 'канцелярия',
 'юридически',
 'значимый',
 'кадровый',
 'документооборот',
 'также',
 'широкий',
 'возможность',
 'развитие',
 'система',
 'подключение',
 'дополнительный',
 'функция',
 'система',
 'настроить',
 'типовой',
 'карточка',
 'работа',
 'договор',
 'письмо',
 'поручение',
 'служебный',
 'записка',
 'приказ',
 'заявление',
 'сотрудник',
 'лна',
 'кадровый',
 'документооборот',
 'также',
 'пред

In [1024]:
concat_text[len(tokenize_text_document):]

['lexema',
 'ecm',
 'иметь',
 'богатый',
 'функционал',
 'типовой',
 'конфигурация',
 'канцелярия',
 'юридически',
 'значимый',
 'кадровый',
 'документооборот',
 'также',
 'широкий',
 'возможность',
 'развитие',
 'система',
 'подключение',
 'дополнительный',
 'функция',
 'система',
 'настроить',
 'типовой',
 'карточка',
 'работа',
 'договор',
 'письмо',
 'поручение',
 'служебный',
 'записка',
 'приказ',
 'заявление',
 'сотрудник',
 'лна',
 'кадровый',
 'документооборот',
 'также',
 'преднастроить',
 'маршрут',
 'обработка',
 'документ',
 'готовый',
 'использование',
 'сразу',
 'развёртывание',
 'система',
 'поэтому',
 'краткий',
 'срок',
 'начать',
 'получать',
 'бонус',
 'электронный',
 'согласование',
 'документ']

In [1025]:
text_document[:100]

'lexema ecm введение введение lexema ecm комплексный система управление корпоративный контент включат'

In [1026]:
lst1 = []
# lst2 = []

In [1027]:
# test_len = len(tokenize_text_test)

In [1028]:
distance_len = len(tokenize_text_test)

In [1029]:
distance_len

55

In [1030]:
for index_text in range(0, len(tokenize_text_document) - distance_len + 1, 1):
    lst1.append(" ".join(tokenize_text_document[index_text:index_text+distance_len]))

In [1031]:
# for index_text in range(0, len(tokenize_text_test), distance_len):
#     lst2.append(" ".join(tokenize_text_test[index_text:index_text+distance_len]))
lst1.append(prep_test_text)

In [1032]:
lst1

['lexema ecm введение введение lexema ecm комплексный система управление корпоративный контент включать автоматизация работа кадровый документ руководство предназначить специалист который необходимо обрабатывать электронный документ lexema ecm создавать карточка отправлять маршрут согласование подписывать документ электронный подпись назначение lexema ecm lexema ecm иметь богатый функционал типовой конфигурация канцелярия юридически значимый кадровый документооборот также широкий возможность развитие система',
 'ecm введение введение lexema ecm комплексный система управление корпоративный контент включать автоматизация работа кадровый документ руководство предназначить специалист который необходимо обрабатывать электронный документ lexema ecm создавать карточка отправлять маршрут согласование подписывать документ электронный подпись назначение lexema ecm lexema ecm иметь богатый функционал типовой конфигурация канцелярия юридически значимый кадровый документооборот также широкий возмож

In [1033]:
tfidf_matrix = vectorizer.fit_transform(lst1)

In [1034]:
similarity_matrix = sklearn_cosine(tfidf_matrix)

In [1035]:
# (lst1 + lst2)[7]

In [1036]:
similarity_matrix[-1]

array([0.26608425, 0.2806863 , 0.29328947, 0.31840006, 0.34142686,
       0.35661607, 0.37351733, 0.38930387, 0.40367424, 0.42336255,
       0.44371695, 0.46431771, 0.48368875, 0.50325773, 0.52374012,
       0.54252013, 0.5631943 , 0.58687024, 0.61063286, 0.63172759,
       0.64513133, 0.6684898 , 0.68949727, 0.70820852, 0.72390935,
       0.74271523, 0.76296511, 0.78608306, 0.8072527 , 0.82933412,
       0.8492219 , 0.86922499, 0.89087445, 0.91125718, 0.92977607,
       0.95101116, 0.97197486, 0.98466377, 1.        , 0.98697205,
       0.97355829, 0.95312516, 0.93165909, 0.91103202, 0.90120268,
       0.88100534, 0.85984077, 0.83884941, 0.8180353 , 0.79875816,
       0.78121996, 0.76283612, 0.74457257, 0.72619018, 0.70866194,
       0.69683801, 0.67520886, 0.65658926, 0.63709863, 0.61822081,
       0.59920625, 0.57660962, 0.55818261, 0.53909473, 0.52032515,
       0.50078565, 0.48450122, 0.46697187, 0.44819528, 0.42816521,
       0.40814079, 0.39019992, 0.3703095 , 0.34625138, 0.32637

In [1037]:
similarity_matrix[-1][:-1]

array([0.26608425, 0.2806863 , 0.29328947, 0.31840006, 0.34142686,
       0.35661607, 0.37351733, 0.38930387, 0.40367424, 0.42336255,
       0.44371695, 0.46431771, 0.48368875, 0.50325773, 0.52374012,
       0.54252013, 0.5631943 , 0.58687024, 0.61063286, 0.63172759,
       0.64513133, 0.6684898 , 0.68949727, 0.70820852, 0.72390935,
       0.74271523, 0.76296511, 0.78608306, 0.8072527 , 0.82933412,
       0.8492219 , 0.86922499, 0.89087445, 0.91125718, 0.92977607,
       0.95101116, 0.97197486, 0.98466377, 1.        , 0.98697205,
       0.97355829, 0.95312516, 0.93165909, 0.91103202, 0.90120268,
       0.88100534, 0.85984077, 0.83884941, 0.8180353 , 0.79875816,
       0.78121996, 0.76283612, 0.74457257, 0.72619018, 0.70866194,
       0.69683801, 0.67520886, 0.65658926, 0.63709863, 0.61822081,
       0.59920625, 0.57660962, 0.55818261, 0.53909473, 0.52032515,
       0.50078565, 0.48450122, 0.46697187, 0.44819528, 0.42816521,
       0.40814079, 0.39019992, 0.3703095 , 0.34625138, 0.32637

In [1038]:
similarity_matrix[-1][:-1].argmax()

np.int64(38)

In [1039]:
find_data = lst1[38]

In [1040]:
find_data

'lexema ecm иметь богатый функционал типовой конфигурация канцелярия юридически значимый кадровый документооборот также широкий возможность развитие система подключение дополнительный функция система настроить типовой карточка работа договор письмо поручение служебный записка приказ заявление сотрудник лна кадровый документооборот также преднастроить маршрут обработка документ готовый использование сразу развёртывание система поэтому краткий срок начать получать бонус электронный согласование документ'

In [1041]:
start_index_preprocessing = text_document.find(find_data)

In [1042]:
end_index_preprocessing = start_index_preprocessing + len(find_data)

In [1043]:
text_document[start_index_preprocessing:end_index_preprocessing]

'lexema ecm иметь богатый функционал типовой конфигурация канцелярия юридически значимый кадровый документооборот также широкий возможность развитие система подключение дополнительный функция система настроить типовой карточка работа договор письмо поручение служебный записка приказ заявление сотрудник лна кадровый документооборот также преднастроить маршрут обработка документ готовый использование сразу развёртывание система поэтому краткий срок начать получать бонус электронный согласование документ'

In [1044]:
text_file = df.loc[2].text_file

In [1045]:
count_other_symbols = (len(text_file) - len(text_document)) * (start_index_preprocessing / len(text_document))

In [1046]:
start_index = round(start_index_preprocessing + count_other_symbols)

In [1047]:
end_index = start_index + len(test_text)

In [1048]:
df.loc[2].text_file[start_index:end_index]

'\n**Lexema-ECM**  имеет богатый функционал типовой конфигурации — от канцелярии до юридически значимого кадрового документооборота, а также широкие возможности для развития системы и подключения дополнительных функций. \nВ системе настроены типовые карточки по работе с договорами, письмами, поручениями, служебными записками, приказами, заявления от сотрудников и ЛНА по кадровому документообороту, а также преднастроены маршруты по их обработке. Документы готовы к использованию сразу после развертывания системы. Поэтому можно в кратчайший срок начать получать бонусы от электронного согласования документов. \n\nВ **L'

In [864]:
# lst_similarity = []

In [728]:
# for i in range(len(lst2)):
#     most_similaratity = np.argpartition(similarity_matrix[::-1][i], -1)[-2:][0]
#     lst_similarity.append([most_similaratity, float(similarity_matrix[::-1][i][most_similaratity])])

In [729]:
# lst_similarity

In [730]:
# index_find = sum([len((lst1 + lst2)[i]) for i in range(3)])

In [731]:
# index_find + 62

In [732]:
# len(lst1)

In [733]:
# 3 / 27

In [734]:
# round((len(df.loc[2].text_file) - len(df.loc[2].text_preprocessing)) * 3 / 27)

In [735]:
# df.loc[2].text_file[422:572]

##### Создании функций для поиска документа по введённой строке

In [1159]:
# Функция для поиска документа по содержимому

def find_document_on_content(input_preprocessing_string: str, count_documents: int = 5) -> list[int]:
    input_string_df = pd.DataFrame({'text_preprocessing' : [input_preprocessing_string]})
    concat_df_test = pd.concat([df, input_string_df], ignore_index=True)['text_preprocessing']
    tfidf_matrix = vectorizer.fit_transform(concat_df_test)
    similarity_matrix = sklearn_cosine(tfidf_matrix)
    cut_similarity_matrix = similarity_matrix[-1][:-1]
    list_max_index_similarity = np.argpartition(cut_similarity_matrix, -1)[-count_documents:][::-1]
    # return [(int(index), float(cut_similarity_matrix[index])) for index in list_max_index_similarity]
    return [int(index) for index in list_max_index_similarity]

# Функция для поиска сходства внутри документа

def split_text(text: str, distance_len) -> list:
    lst = []
    text_tokenize = word_tokenize(text)
    for index_text in range(0, len(text_tokenize) - distance_len + 1, 1):
        lst.append(" ".join(text_tokenize[index_text:index_text+distance_len]))
    return lst

def find_index_data(text_document: str, text_document_preprocessing: str, find_data: str, count_char_out_sent: int = 350):
    start_index_preprocessing = text_document_preprocessing.find(find_data)
    count_other_symbols = (len(text_document) - len(text_document_preprocessing)) * (start_index_preprocessing / len(text_document_preprocessing))
    start_index = round(start_index_preprocessing + count_other_symbols)
    end_index = start_index + count_char_out_sent
    return start_index, end_index
    
def find_position_on_document(index_document: int, input_preprocessing_string: str) -> (int, int):
    text_document = df.loc[index_document].text_file
    text_document_preprocessing = df.loc[index_document].text_preprocessing
    
    lst_split_text = split_text(text_document_preprocessing, len(word_tokenize(input_preprocessing_string)))
    lst_split_text.append(input_preprocessing_string)
    
    tfidf_matrix = vectorizer.fit_transform(lst_split_text)
    similarity_matrix = sklearn_cosine(tfidf_matrix)
    index_max_similarity = similarity_matrix[-1][:-1].argmax()
    
    return find_index_data(text_document, text_document_preprocessing, lst_split_text[index_max_similarity])

# Функция поиска всех документов и совпадений в них
def find_documents(input_string):
    input_preprocessing_string = text_preprocessing(input_string)
    find_id_documents = find_document_on_content(input_preprocessing_string)
    list_data_documents = []
    for index in find_id_documents:
        doc = df.loc[index]
        start_index, end_index = find_position_on_document(index, input_preprocessing_string)
        list_data_documents.append({
            "name_file" : doc.name_file,
            "date_last_modified_file" : doc.date_last_modified_file,
            "find_similarity" : doc.text_file[start_index:end_index]
        })
    return list_data_documents

In [1118]:
# input_preprocessing_string = text_preprocessing(test_text)
input_preprocessing_string = text_preprocessing("Создание пользователя SchedulerUser")

In [1120]:
find_document_on_content(input_preprocessing_string)

[114, 100, 248, 184, 264]

In [1121]:
df.loc[114]

name_file                                                       index (2).md
text_file                  ---\nsearch:\n  boost: 3 \n---\n# Автоматическ...
date_last_modified_file                                     02-12-2025 15:02
text_preprocessing         search boost автоматический создание пользоват...
Name: 114, dtype: object

In [1155]:
find_position_on_document(114, input_preprocessing_string)

(72, 422)

In [1123]:
df.loc[114].text_file[72:422]

'Создание пользователей\n\nПользователь, выполняющий функцию автоматической загрузки пользователей, должен обладать правами администратора.\n\nДля автоматического создания пользователей необходимо:\n\n* Установить последнюю версию вспомогательной **библиотеки функций управления пользователями для планировщика задач**.\n* Установить последнюю версию библиот'

##### Текст из файла:

**Lexema-ECM** — комплексная система управления корпоративным контентом, включающая в себя автоматизацию работы с кадровыми документами.

##### Текст из файла после синонимазера

Lexema-ECM — это универсальное решение для организации и управления всеми документами вашей компании, которое также помогает автоматизировать процессы, связанные с кадровой документацией.
С помощью Lexema-ECM вы сможете эффективно управлять корпоративным контентом и упростить работу с документами отдела кадров.

In [1163]:
find_documents("Lexema-ECM — это универсальное решение для организации и управления всеми документами вашей компании, которое также помогает автоматизировать процессы, связанные с кадровой документацией. С помощью Lexema-ECM вы сможете эффективно управлять корпоративным контентом и упростить работу с документами отдела кадров.")

[{'name_file': 'description.md',
  'date_last_modified_file': '08-12-2025 12:09',
  'find_similarity': ' записки и т.п.\n\nLexema-ECM располагает всеми необходимыми возможностями для ведения учета и регистрации этих документов.\n\nLexema-ECM - комплексная система управления корпоративным контентом для средних и крупных компаний с функциями корпоративного обучения, кадрового документооборота, распознавания и обработки первичных\nдокументов. Решение предост'},
 {'name_file': 'index (182).md',
  'date_last_modified_file': '08-12-2025 12:09',
  'find_similarity': 'е записки и т.п.\n\nLexema-ECM располагает всеми необходимыми возможностями для ведения учета и регистрации этих документов.\n\nLexema-ECM - комплексная система управления корпоративным контентом для средних и крупных компаний с функциями корпоративного обучения, кадрового документооборота, распознавания и обработки первичных\nдокументов. Решение предос'},
 {'name_file': 'Service (1).md',
  'date_last_modified_file': '27-11-2025 

##### Сохранение векторизации

In [20]:
with open('vectorizer.pkl', 'wb') as file:
    dump(vectorizer, file)